<a href="https://colab.research.google.com/github/custom-hyper/Research/blob/main/watchlist_report.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
#@title Connect to FNS { display-mode: "code" }
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [2]:
#@title Install Libraries { display-mode: "code" }
!pip install plotly
!pip install pytrends
!pip install pycoingecko
!pip install pandas
!pip install tweepy
!pip install requests
!pip install pipreqs
!pip install configparser
!pip install psycopg2
!pip install dash

In [3]:
#@title Import Project  Dependencies { display-mode: "code" }
import requests
import datetime
import time
import json
from google.colab import data_table
import plotly.graph_objects as go
import pandas as pd
import matplotlib.pyplot as plt
from pandas.io.json import json_normalize
import logging
import sys
from tqdm.notebook import tqdm
import os
import sqlite3 as sq
import psycopg2 as pg
import configparser
from sqlalchemy import create_engine
from pycoingecko import CoinGeckoAPI
import glob
from pathlib import Path
from __future__ import division

/usr/local/lib/python3.7/dist-packages/psycopg2/__init__.py:144: UserWarning: The psycopg2 wheel package will be renamed from release 2.8; in order to keep installing from binary please use "pip install psycopg2-binary" instead. For details see: <http://initd.org/psycopg/docs/install.html#binary-install-from-pypi>.
  """)


## Setup SQLite


In [4]:
#@title  Connect { display-mode: "code" }
path = '/content/drive/MyDrive/workspace/pipelines/db/' #@param {type: 'string'
database = "db.sqlite" #@param {type: 'string'
conn_SQLite = sq.connect(path+database)

In [5]:
#@title   Show Available Tables { display-mode: "code" }
cursor = conn_SQLite.cursor()

cursor.execute("SELECT name FROM sqlite_master WHERE type='table';")
cursor.fetchall()

[('deFi_lama_total_TVL',),
 ('proprietary_Twitter_Partnership_ohlc',),
 ('proprietary_master_id',),
 ('CoinGecko_ohlc',),
 ('proprietary_tweets_extract',),
 ('proprietary_Twitter_partnerships_announcements',),
 ('deFi_lama_tvl',),
 ('proprietary_Twitter_id',),
 ('deFi_lama_general',),
 ('proprietary_airtable_watch_all',),
 ('proprietary_dashboard',),
 ('watchlist_CoinGecko_ohlc',)]

In [6]:
#@title Load Token ID to SQLite { display-mode: "code" }
proprietary_airtable_watch_all  = "proprietary_airtable_watch_all"


df_proprietary_airtable_shortlisted = pd.read_sql("""
          select *
          from {} 
        
          WHERE status = 'Shortlisted'
          And CoinGecko_id not null
          """.format(proprietary_airtable_watch_all), conn_SQLite)

df_proprietary_airtable_shortlisted.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 99 entries, 0 to 98
Data columns (total 61 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   id                     94 non-null     object 
 1   close watch            39 non-null     object 
 2   CoinGecko_id           99 non-null     object 
 3   yahoo_id               0 non-null      object 
 4   update                 2 non-null      object 
 5   status                 99 non-null     object 
 6   Count (Memo)           99 non-null     int64  
 7   org_type               50 non-null     object 
 8   Investors_found        9 non-null      object 
 9   investors_list         72 non-null     object 
 10  theme                  70 non-null     object 
 11  theme_rating           69 non-null     object 
 12  thesis                 70 non-null     object 
 13  personal_questions     12 non-null     object 
 14  vision                 11 non-null     object 
 15  descript

In [7]:

token_list = df_proprietary_airtable_shortlisted['CoinGecko_id']
frames = []

try:

  for i in tqdm(token_list[: 3]):

    #General Information table
    response = requests.get("https://api.coingecko.com/api/v3/coins/{}".format(i))
    output = response.text
    json_parsed = json.loads(output)
    
    df= pd.DataFrame()
    
    df['market_cap'] = json_parsed['market_data']['market_cap']['usd']
    df['circulating_supply'] = json_parsed['market_data']['circulating_supply']  
    df['current_price'] = json_parsed['market_data']['current_price']['usd']  
    df['fdv_to_tvl_ratio'] = json_parsed['market_data']['fdv_to_tvl_ratio']  
    #df['fully_diluted_valuation'] = json_parsed['market_data']['fully_diluted_valuation']['usd']
    df['price_change_24h'] = json_parsed['market_data']['price_change_24h'] 
    #df['max_supply'] = json_parsed['market_data']['max_supply']['usd']
    df['mcap_to_tvl_ratio'] = json_parsed['market_data']['mcap_to_tvl_ratio']
    df['total_supply'] = json_parsed['market_data']['total_supply']
    #df['total_value_locked'] = json_parsed['market_data']['total_value_locked']
    df['total_volume'] = json_parsed['market_data']['total_volume']['usd']

    df['dollar_volume_rotation']  = df['total_volume'] / df['market_cap']
    #df['supply_expansion_multiple'] = df['max_supply']/df['circulating_supply']
    
    df['CoinGecko_id'] = str(i)
    df['price_change_percentage_7d'] = json_parsed['market_data']['price_change_percentage_7d']
    df['price_change_percentage_14d'] = json_parsed['market_data']['price_change_percentage_14d']
    df['price_change_percentage_30d'] = json_parsed['market_data']['price_change_percentage_30d']
    df['price_change_percentage_60d'] = json_parsed['market_data']['price_change_percentage_60d']
    df['price_change_percentage_200d'] = json_parsed['market_data']['price_change_percentage_200d']
    df['price_change_percentage_1y'] = json_parsed['market_data']['price_change_percentage_1y']

    frames.append(df)
    time.sleep(60/50)
except ConnectionError:
    time.sleep(60)
single = pd.concat(frames) #Careful, this line must be outside of the for loop
single['prop_timestamp'] = int( time.time_ns() / 1000 )



"""    
    df['circulating_versus_max'] = circulating_supply/total_supply
    df['market_cap_dilution_ratio'] =  fully_diluted_valuation / market_cap
      
          
    df['dollar_volume_rotation'] = dollar_volume_rotation
    df['['supply_expansion_multiple'] = supply_expansion_multiple
    df['circulating_versus_max'] = circulating_versus_max
    df['market_cap_dilution_ratio'] = market_cap_dilution_ratio - 1
    except ZeroDivisionError:
      print('null')
      

    
    #df_market = pd.DataFrame(data=mkdata, columns = ['market_cap','current_price','fdv_to_tvl_ratio','fully_diluted_valuation','mcap_to_tvl_ratio'])
    
    print(df_market)


    
    print(dict_return)



    category = json_parsed['categories']

    print('')  
    print('CATEGORIES')  
    print(category)
    
    
    
    community_data = json_parsed['community_data']

    df_community_data = pd.DataFrame(data=community_data, index=[0])
    #pd.set_option("display.max_rows", None, "display.max_columns", None)
    print('')  
    print('COMMUNITY DATA')
    print(community_data)

    from google.colab import data_table
    data_table.DataTable(df_community_data)
    
    community_score = json_parsed['community_score']
    
    description  = [] 
    pd.set_option('display.width', 10)
    pd.set_option("display.max_rows", None, "display.max_columns", None)
    description = json_parsed['description']['en']
    
    print('')  
    print('DESCRIPTION: ')
    print(description)

    print('')  
    print('DEVELOPER ACTIVITY')
    developer_data = json_parsed['developer_data']
    print(developer_data)
    
    genesis_date = json_parsed['genesis_date']
    print('')
    print('GENESIS DATE')
    print(genesis_date)
    
    links = json_parsed['links']
    
    pd.set_option('display.width', 10)

    print('')
    print('WEB Links')
    print(links)

    #Status update

    response = requests.get("https://api.coingecko.com/api/v3/coins/{}/status_updates".format(i))
    output = response.text
    json_parsed_Updates = json.loads(output)
    print('')
    print('Recent updates: ')
    print(json_parsed_Updates)
    try:  
      a = cg.get_coin_ohlc_by_id(id=i, vs_currency='usd', days = 'max')
    except:
        pass
    df = pd.DataFrame(data=a, columns = ['Date','Open','High', 'Low', 'Close'])
    
    
    
    fig2 = go.Figure(data=[go.Candlestick(x=df['Date'],open=df['Open'], high=df['High'],low=df['Low'], close=df['Close'])])
    
    
    fig2.show()
"""   


  0%|          | 0/3 [00:00<?, ?it/s]

'    \n    df[\'circulating_versus_max\'] = circulating_supply/total_supply\n    df[\'market_cap_dilution_ratio\'] =  fully_diluted_valuation / market_cap\n      \n          \n    df[\'dollar_volume_rotation\'] = dollar_volume_rotation\n    df[\'[\'supply_expansion_multiple\'] = supply_expansion_multiple\n    df[\'circulating_versus_max\'] = circulating_versus_max\n    df[\'market_cap_dilution_ratio\'] = market_cap_dilution_ratio - 1\n    except ZeroDivisionError:\n      print(\'null\')\n      \n\n    \n    #df_market = pd.DataFrame(data=mkdata, columns = [\'market_cap\',\'current_price\',\'fdv_to_tvl_ratio\',\'fully_diluted_valuation\',\'mcap_to_tvl_ratio\'])\n    \n    print(df_market)\n\n\n    \n    print(dict_return)\n\n\n\n    category = json_parsed[\'categories\']\n\n    print(\'\')  \n    print(\'CATEGORIES\')  \n    print(category)\n    \n    \n    \n    community_data = json_parsed[\'community_data\']\n\n    df_community_data = pd.DataFrame(data=community_data, index=[0])\n   

In [8]:
#@title Create proprietary_dashboard to SQLite { display-mode: "code" }
 
proprietary_dashboard = "proprietary_dashboard"

single.to_sql(proprietary_dashboard, conn_SQLite, if_exists='replace', index=False) # writes to file
conn_SQLite.commit()

# Just be sure any changes have been committed or they will be lost.

proprietary_dashboard = pd.read_sql('select * from {}'.format(proprietary_dashboard), conn_SQLite)

proprietary_dashboard.info()

<class 'pandas.core.frame.DataFrame'>
Index: 0 entries
Data columns (total 17 columns):
 #   Column                        Non-Null Count  Dtype 
---  ------                        --------------  ----- 
 0   market_cap                    0 non-null      object
 1   circulating_supply            0 non-null      object
 2   current_price                 0 non-null      object
 3   fdv_to_tvl_ratio              0 non-null      object
 4   price_change_24h              0 non-null      object
 5   mcap_to_tvl_ratio             0 non-null      object
 6   total_supply                  0 non-null      object
 7   total_volume                  0 non-null      object
 8   dollar_volume_rotation        0 non-null      object
 9   CoinGecko_id                  0 non-null      object
 10  price_change_percentage_7d    0 non-null      object
 11  price_change_percentage_14d   0 non-null      object
 12  price_change_percentage_30d   0 non-null      object
 13  price_change_percentage_60d   0 non-n

In [9]:


path = "/content/drive/MyDrive/workspace/pipelines/datasets/coingecko/ohlc/watchlist/output/bulk/"


Cleaned_data_file = 'watchlist_Bulk_CoinGecko_ohlc.csv'

df = pd.DataFrame()

extension = 'csv'
#dataset_location = os.chdir(r'D:\investing_programs\datasets\CoinMetrics')
all_filenames = []
all_filenames = [i for i in glob.glob('/content/drive/MyDrive/workspace/pipelines/datasets/coingecko/ohlc/watchlist/output/*.{}'.format(extension))]

#combine all files in the list
for i in all_filenames:
    df = pd.read_csv(i)#.read(),engine='openpyxl')   
    

combined_csv = df.append([pd.read_csv(f) for f in all_filenames])

del combined_csv['Unnamed: 0']

combined_csv.to_csv( path + Cleaned_data_file, index=False, encoding='utf-8-sig')


print(combined_csv.head())




            Date   Open   High    Low  Close CoinGecko_id    prop_timestamp
0  1620345600000  30.05  30.05  30.05  30.05      adamant  1651608571499549
1  1620691200000  77.62  77.62  37.21  37.21      adamant  1651608571499549
2  1621036800000  35.87  49.95  33.55  37.57      adamant  1651608571499549
3  1621382400000  39.16  45.40  39.16  45.40      adamant  1651608571499549
4  1621728000000  32.23  32.23  24.31  24.31      adamant  1651608571499549


In [10]:
#@title Load watchlist_CoinGecko_ohlc to SQLite { display-mode: "code" }

watchlist_CoinGecko_ohlc = "watchlist_CoinGecko_ohlc"

combined_csv.to_sql(watchlist_CoinGecko_ohlc, conn_SQLite, if_exists='replace', index=False) # writes to file
conn_SQLite.commit()

# Just be sure any changes have been committed or they will be lost.

watchlist_CoinGecko_ohlc = pd.read_sql('select * from {}'.format(watchlist_CoinGecko_ohlc), conn_SQLite)

In [11]:
watchlist_CoinGecko_ohlc.head()
watchlist_CoinGecko_ohlc['Datetime'] = pd.to_datetime(watchlist_CoinGecko_ohlc['Date'], unit='ms')
 
watchlist_CoinGecko_ohlc['Datetime']

0       2021-05-07
1       2021-05-11
2       2021-05-15
3       2021-05-19
4       2021-05-23
           ...    
60099   2022-04-19
60100   2022-04-23
60101   2022-04-27
60102   2022-04-30
60103   2022-05-03
Name: Datetime, Length: 60104, dtype: datetime64[ns]

In [12]:
watchlist_CoinGecko_ohlc.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 60104 entries, 0 to 60103
Data columns (total 8 columns):
 #   Column          Non-Null Count  Dtype         
---  ------          --------------  -----         
 0   Date            60104 non-null  int64         
 1   Open            60104 non-null  float64       
 2   High            60104 non-null  float64       
 3   Low             60104 non-null  float64       
 4   Close           60104 non-null  float64       
 5   CoinGecko_id    60104 non-null  object        
 6   prop_timestamp  60104 non-null  int64         
 7   Datetime        60104 non-null  datetime64[ns]
dtypes: datetime64[ns](1), float64(4), int64(2), object(1)
memory usage: 3.7+ MB


In [52]:
#@title Generate Report { display-mode: "code" }



cg = CoinGeckoAPI()
CoinGecko_id = df_proprietary_airtable_shortlisted['CoinGecko_id'].unique()

days = ['max','30','1']
vs_currency = ['usd']

frames = []
b_March = []
df_desc = {}


frames_description = []


try:

  for i in tqdm(CoinGecko_id[:]):

      try:          
        b = cg.get_coin_by_id(id=i)
      except:
          pass
     

      # description  
      market_cap = df_desc['market_cap'] = b['market_data']['market_cap']['usd']
      df_desc['asset_platform_id'] = b['asset_platform_id']
      twitter_followers = df_desc['twitter_followers'] = b['community_data']['twitter_followers']
      df_desc['categories'] = b['categories']
      df_desc['categories'] = b['categories']
      df_desc['categories'] = b['categories']
      df_desc['price_change_24h'] = b['market_data']['price_change_24h'] 
      df_desc['total_volume'] = b['market_data']['total_volume']['usd']
      circulating_supply = df_desc['circulating_supply'] = b['market_data']['circulating_supply']
      df_desc['description'] = b['description']['en']
      try: 
        fully_diluted_valuation = df_desc['fully_diluted_valuation'] = b['market_data']['fully_diluted_valuation']['usd']
      except:
        pass

      df_desc['fdv_to_tvl_ratio'] = b['market_data']['fdv_to_tvl_ratio']
      df_desc['mcap_to_tvl_ratio'] = b['market_data']['mcap_to_tvl_ratio']
      total_supply = df_desc['total_supply'] = b['market_data']['total_supply']
      df_desc['coingecko_score'] = b['coingecko_score'] 
      df_desc['homepage'] = b['links']['homepage'] 
      df_desc['ath_change_percentage'] = b['market_data']['ath_change_percentage']['usd'] 

      try: 
        df_desc['circulating_versus_max'] = circulating_supply/total_supply
      except:
        pass

      try: 
        df_desc['market_cap_dilution_ratio'] =  fully_diluted_valuation / market_cap
      except:
        pass
      try: 
        market_cap_per_twitter_followers = market_cap/twitter_followers
      except:
        pass      
      df_desc['announcement_url'] = b['links']['announcement_url']
      df_desc['official_forum_url'] = b['links']['official_forum_url']
      df_desc['twitter_screen_name'] = b['links']['twitter_screen_name']
      df_desc['chat_url'] = b['links']['chat_url']
      df_desc['name'] = b['name']
      df_desc['symbol'] = b['symbol']
      df_desc['asset_platform_id'] = b['asset_platform_id']
      df_desc['sentiment_votes_down_percentage'] = b['sentiment_votes_down_percentage']
      df_desc['sentiment_votes_up_percentage'] = b['sentiment_votes_up_percentage']
    #Convert data to list of dataframes
      full_table = pd.json_normalize(df_desc)
    #results = [full_table]
      frames_description.append(full_table)
      #print(full_table)

              # REPORT
      print('')  
      print('('+str(df_desc['symbol'].upper())+') '+str(df_desc['name']))  
      print(str(df_desc['asset_platform_id']))
      print(str('categories: ')+str(df_desc['categories']))
      print('')  
      print('Statistics')
      print('--------------------------------------------------------')
      print(
          str('sentiment: ') +
          str(df_desc['sentiment_votes_up_percentage']) +
          str(' up vs ')+
          str(df_desc['sentiment_votes_down_percentage']))
      
      print(str('market_cap: ')+str('{:0,}'.format(df_desc['market_cap'])))
      if df_desc['fdv_to_tvl_ratio'] != None:
        print(str('fdv_to_tvl_ratio: ')+str('{:0,}'.format(df_desc['fdv_to_tvl_ratio'])))
      print(str('price_change_24h: ')+str('{:0,.1f}'.format(df_desc['price_change_24h']))+str('%'))
      print(str('ath %: ')+str('{:0,.1f}'.format(df_desc['ath_change_percentage']))+str('%'))
      print(str('coingecko_score: ')+str(df_desc['coingecko_score']))
      print('')        
      print('Tokenomics')
      print('--------------------------------------------------------')        
      print(str('circ_vs_max: ')+str('{:0,.1f}'.format(df_desc['circulating_versus_max'])))
      print(str('market_cap_dilution_ratio: ')+str('{:0,.1f}'.format(df_desc['market_cap_dilution_ratio'])))
      if df_desc['mcap_to_tvl_ratio'] != None:
        print(str('mcap_to_tvl_ratio: ')+str('{:0,.1f}'.format(df_desc['mcap_to_tvl_ratio'])))
      print('')        
      print('Description')
      print('--------------------------------------------------------')
      print(str(df_desc['description']))
      print('')        
      print('Social')
      print('--------------------------------------------------------')
      print(str('market_cap_per_twitter_followers: ')+str('{:0,}'.format(market_cap_per_twitter_followers)))
      print('')        
      print('Links')
      print('--------------------------------------------------------')
      print(str('homepage: ')+str(df_desc['homepage']))
      print(str('announcements: ')+str(df_desc['announcement_url']))
      print(str('forum: ')+str(df_desc['official_forum_url']))
      print(str('chat: ')+str(df_desc['chat_url']))
      print(str('Twitter: ')+str('https://twitter.com/')+str(df_desc['twitter_screen_name']))
      print(str('Reddit: ')+str(df_desc['homepage']))


      for day in days:
    
        try:  
          a = cg.get_coin_ohlc_by_id(
            id=i,
            vs_currency='usd',
            days = day)

        except:
            pass
   
       
        # Create dataframe and Chart 
        df = pd.DataFrame(data=a, columns = ['Date','Open','High', 'Low', 'Close'])
        df['CoinGecko_id'] = str(i)
        df['Datetime'] = pd.to_datetime(df['Date'], unit='ms')

        trace1 = {
        'x': df.Datetime,
        'open': df.Open,
        'close': df.Close,
        'high': df.High,
        'low': df.Low,
        'type': 'candlestick',
        'name': str(i).upper(),
        'showlegend': True
        }

      
        # Calculate and define moving average of 30 periods
        avg_10 = df.Close.rolling(window=10, min_periods=1).mean()
        # Calculate and define moving average of 50 periods
        avg_20 = df.Close.rolling(window=20, min_periods=1).mean()
        # Calculate and define moving average of 30 periods
        avg_50 = df.Close.rolling(window=50, min_periods=1).mean()
        # Calculate and define moving average of 50 periods
        avg_100 = df.Close.rolling(window=100, min_periods=1).mean()


        trace2 = {
            'x': df.Datetime,
            'y': avg_10,
            'type': 'scatter',
            'mode': 'lines',
            'line': {
                'width': 1,
                'color': 'purple'
                    },
            'name': 'Moving Average of 10 periods'
        }

        trace3 = {
            'x': df.Datetime,
            'y': avg_20,
            'type': 'scatter',
            'mode': 'lines',
            'line': {
                'width': 1,
                'color': 'orange'
            },
            'name': 'Moving Average of 20 periods'
        }
        trace4 = {
            'x': df.Datetime,
            'y': avg_50,
            'type': 'scatter',
            'mode': 'lines',
            'line': {
                'width': 1,
                'color': 'green'
                    },
            'name': 'Moving Average of 50 periods'
        }

        trace5 = {
            'x': df.Datetime,
            'y': avg_100,
            'type': 'scatter',
            'mode': 'lines',
            'line': {
                'width': 1,
                'color': 'blue'
            },
            'name': 'Moving Average of 100 periods'
        }
        data = [trace1, trace2, trace3,trace4,trace5]
        # Config graph layout
        layout = go.Layout({
            'title': {
                'text': str(i).upper().replace("-"," ") + ' Moving Averages',
                'font': {
                    'size': 15
                }
            }
        })



        
                
        #CHARTING



        fig = go.Figure(data=data, layout=layout)
        fig.show()
        CoinGeckoAPI
        time.sleep(60/50)



except ConnectionError:
    time.sleep(60)

fig.write_html("Moving Averages.html")


  0%|          | 0/97 [00:00<?, ?it/s]


(ZRX) 0x
ethereum
categories: ['Protocol', 'Decentralized Finance (DeFi)', 'Governance', 'Polkadot Ecosystem', 'Decentralized Exchange Token (DEX)', 'Polygon Ecosystem', None]

Statistics
--------------------------------------------------------
sentiment: 76.47 up vs 23.53
market_cap: 691,960,099
price_change_24h: 0.1%
ath %: -67.5%
coingecko_score: 54.531

Tokenomics
--------------------------------------------------------
circ_vs_max: 0.8
market_cap_dilution_ratio: 1.2

Description
--------------------------------------------------------


Social
--------------------------------------------------------
market_cap_per_twitter_followers: 2,649.4928494028727

Links
--------------------------------------------------------
homepage: ['https://0x.org/', '', '']
announcements: ['https://blog.0xproject.com/', '']
forum: ['', '', '']
chat: ['https://discord.com/invite/FduK2mE', '', '']
Twitter: https://twitter.com/0xproject
Reddit: ['https://0x.org/', '', '']



(ALGO) Algorand
None
categories: ['Cryptocurrency', 'Smart Contract Platform']

Statistics
--------------------------------------------------------
sentiment: 84.8 up vs 15.2
market_cap: 4,851,351,995
price_change_24h: 0.0%
ath %: -79.8%
coingecko_score: 60.71

Tokenomics
--------------------------------------------------------
circ_vs_max: 0.9
market_cap_dilution_ratio: 1.5

Description
--------------------------------------------------------
Algorand is a scalable, secure and decentralized digital currency and transactions platform.

Social
--------------------------------------------------------
market_cap_per_twitter_followers: 18,067.609874455797

Links
--------------------------------------------------------
homepage: ['https://algorand.foundation/', 'https://www.algorand.com/', 'https://www.algorand.com/resources']
announcements: ['https://medium.com/algorand', 'https://forum.algorand.org/']
forum: ['', '', '']
chat: ['https://discord.gg/QBYp7Y2', '', '']
Twitter: https://twitt


(AVAX) Avalanche
avalanche
categories: ['Avalanche Ecosystem', 'Polygon Ecosystem', None, None, 'Smart Contract Platform']

Statistics
--------------------------------------------------------
sentiment: 81.53 up vs 18.47
market_cap: 18,358,168,420
price_change_24h: 8.8%
ath %: -52.8%
coingecko_score: 62.804

Tokenomics
--------------------------------------------------------
circ_vs_max: 0.7
market_cap_dilution_ratio: 2.7

Description
--------------------------------------------------------
Avalanche is a high throughput smart contract blockchain platform. Validators secure the network through a proof-of-stake consensus protocol. It is said to be fast, low cost, and environmental friendly.

Mainnet was launched in September 21, 2020. Since then, the platform has grown to secure over 100+ individual projects, $1.4M+ of AVAX burned (reducing supply), 950+ individual block-producing validators, and over 500k+ community members around the globe. Decentralized finance (DeFi) applications c


(BAL) Balancer
ethereum
categories: ['Decentralized Exchange Token (DEX)', 'Governance', 'Decentralized Finance (DeFi)', 'Exchange-based Tokens', 'Yield Farming', 'Automated Market Maker (AMM)', 'Near Protocol Ecosystem', 'Polygon Ecosystem', 'Arbitrum Ecosystem', None]

Statistics
--------------------------------------------------------
sentiment: 57.14 up vs 42.86
market_cap: 155,812,571
fdv_to_tvl_ratio: 0.44
price_change_24h: 1.5%
ath %: -80.5%
coingecko_score: 41.67

Tokenomics
--------------------------------------------------------
circ_vs_max: 0.2
market_cap_dilution_ratio: 9.3
mcap_to_tvl_ratio: 0.1

Description
--------------------------------------------------------
Balancer is a non-custodial portfolio manager, liquidity provider, and price sensor

The Balancer Protocol Governance Token (BAL) are distributed to Liquidity Providers of Balancer. BALs are a key way of decentralizing the governance of the protocol such that it can remain resilient over time, protected from the

...


(LQTY) Liquity
ethereum
categories: ['Lending/Borrowing', 'Decentralized Finance (DeFi)', None]

Statistics
--------------------------------------------------------
sentiment: 71.43 up vs 28.57
market_cap: 114,956,936
fdv_to_tvl_ratio: 0.15
price_change_24h: 0.1%
ath %: -98.9%
coingecko_score: 25.161

Tokenomics
--------------------------------------------------------
circ_vs_max: 0.7
market_cap_dilution_ratio: 1.4
mcap_to_tvl_ratio: 0.1

Description
--------------------------------------------------------
LQTY is a token that captures the fee revenue generated by the Liquity Protocol via staking. Liquity is a decentralized borrowing protocol that allows you to draw 0% interest loans against Ether used as collateral. Loans are paid out in LUSD and need to maintain a minimum collateral ratio of only 110%.

In addition to the collateral, the loans are secured by a Stability Pool containing LUSD and by fellow borrowers collectively acting as guarantors of last resort. 

Liquity as a prot


(BOSON) Boson Protocol
ethereum
categories: ['Metaverse', 'Non-Fungible Tokens (NFT)', None]

Statistics
--------------------------------------------------------
sentiment: 81.25 up vs 18.75
market_cap: 59,430,516
price_change_24h: 0.1%
ath %: -86.1%
coingecko_score: 21.304

Tokenomics
--------------------------------------------------------
circ_vs_max: 0.4
market_cap_dilution_ratio: 2.5

Description
--------------------------------------------------------
Boson Protocol is a trust minimised and cost minimised protocol that automates digital to physical redemptions using NFTs encoded with game theory.

Boson Protocol’s vision is to enable a decentralized commerce ecosystem by funding and accelerating the development of a stack of specialist applications to disrupt, unbundle and democratize commerce.

What is needed is a way to execute commerce transactions trustlessly with minimized human intermediaries or arbitrators. Our core technology disrupts e-commerce platforms by tokenizing r


(GRT) The Graph
ethereum
categories: ['Analytics', 'Business Services', 'Infrastructure', 'Decentralized Finance (DeFi)', 'Solana Ecosystem', 'Polygon Ecosystem', 'Binance Smart Chain Ecosystem', 'Near Protocol Ecosystem', 'xDAI Ecosystem', 'Avalanche Ecosystem', 'Arbitrum Ecosystem', None]

Statistics
--------------------------------------------------------
sentiment: 62.5 up vs 37.5
market_cap: 2,356,708,125
price_change_24h: 0.0%
ath %: -88.0%
coingecko_score: 59.451

Tokenomics
--------------------------------------------------------
circ_vs_max: 0.7
market_cap_dilution_ratio: 1.4

Description
--------------------------------------------------------
The Graph is an indexing protocol and global API for organizing blockchain data and making it easily accessible with GraphQL. Developers can use Graph Explorer to search, find, and publish all the public data they need to build decentralized applications. The Graph Network makes it possible to build serverless dApps that run entirely o


(API3) API3
ethereum
categories: ['Oracle', 'Decentralized Finance (DeFi)', 'Number', 'Polygon Ecosystem', None, 'Near Protocol Ecosystem', None]

Statistics
--------------------------------------------------------
sentiment: 81.25 up vs 18.75
market_cap: 190,775,208


ValueError: ignored

In [39]:
df = pd.DataFrame()

b




#.categories

{'additional_notices': [],
 'asset_platform_id': None,
 'block_time_in_minutes': 0,
 'categories': ['Smart Contract Platform', None],
 'coingecko_rank': 2,
 'coingecko_score': 77.238,
 'community_data': {'facebook_likes': None,
  'reddit_accounts_active_48h': 1088,
  'reddit_average_comments_48h': 186.222,
  'reddit_average_posts_48h': 4.889,
  'reddit_subscribers': 1267551,
  'telegram_channel_user_count': None,
  'twitter_followers': 2454465},
 'community_score': 59.539,
 'country_origin': '',
 'description': {'ar': '',
  'bg': 'Ethereum is a <a href="https://www.coingecko.com/en?category_id=29&view=market">smart contract platform</a> that enables developers to build tokens and decentralized applications (dapps). ETH is the native currency for the Ethereum platform and also works as the transaction fees to miners on the Ethereum network.\r\n\r\nEthereum is the pioneer for blockchain based smart contracts. Smart contract is essentially a computer code that runs exactly as programmed w

In [ ]:
PS:b.info()